## **Step 1: Setting Up ExecuTorch**

In [ ]:
! touch /content/executorch; rm -rf /content/executorch
! git clone https://github.com/pytorch/executorch ; cd /content/executorch; git checkout dfbf6fd53546eb86e18f2e5cc693d70a82e3b03f; git submodule sync ; git submodule update --init

Cloning into 'executorch'...
remote: Enumerating objects: 154340, done.
remote: Counting objects: 100% (1179/1179), done.
remote: Compressing objects: 100% (522/522), done.
remote: Total 154340 (delta 744), reused 995 (delta 636), pack-reused 153161 (from 1)
Receiving objects: 100% (154340/154340), 140.71 MiB | 19.41 MiB/s, done.
Resolving deltas: 100% (121299/121299), done.
Note: switching to 'dfbf6fd53546eb86e18f2e5cc693d70a82e3b03f'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false

HEAD is now at dfbf6fd53 Mention torchao i

In [ ]:
# This is a workaround for now
!mkdir -p /usr/lib/python3/dist-packages/torchgen/packaged/ATen/native/
!cp /usr/local/lib/python3.10/dist-packages/torchgen/packaged/ATen/native/* /usr/lib/python3/dist-packages/torchgen/packaged/ATen/native/

In [22]:
import sysconfig; lib_path = sysconfig.get_paths()["purelib"]
! cd /content/executorch; CMAKE_PREFIX_PATH={lib_path} EXECUTORCH_BUILD_XNNPACK=ON bash ./install_requirements.sh --pybind

Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/nightly/cpu
Using pip 24.1.2 from /usr/local/lib/python3.10/dist-packages/pip (python 3.10)
Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/nightly/cpu
Processing /content/executorch
  Running command Preparing metadata (pyproject.toml)
  running dist_info
  creating /tmp/pip-modern-metadata-bz09i4op/executorch.egg-info
  writing /tmp/pip-modern-metadata-bz09i4op/executorch.egg-info/PKG-INFO
  writing dependency_links to /tmp/pip-modern-metadata-bz09i4op/executorch.egg-info/dependency_links.txt
  writing entry points to /tmp/pip-modern-metadata-bz09i4op/executorch.egg-info/entry_points.txt
  writing requirements to /tmp/pip-modern-metadata-bz09i4op/executorch.egg-info/requires.txt
  writing top-level names to /tmp/pip-modern-metadata-bz09i4op/executorch.egg-info/top_level.txt
  writing manifest file '/tmp/pip-modern-metadata-bz09i4op/executorch.egg-info/SOURCES.txt'
  reading man

In [ ]:
!cd /content/executorch; examples/models/llama/install_requirements.sh

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.5/183.5 kB 3.6 MB/s eta 0:00:00
  Cloning https://github.com/pytorch/ao.git (to revision 0916b5b29b092afcbf2b898caae49abe80662bac) to /tmp/pip-req-build-srblgunz
  Running command git clone --filter=blob:none --quiet https://github.com/pytorch/ao.git /tmp/pip-req-build-srblgunz
  Running command git rev-parse -q --verify 'sha^0916b5b29b092afcbf2b898caae49abe80662bac'
  Running command git fetch -q https://github.com/pytorch/ao.git 0916b5b29b092afcbf2b898caae49abe80662bac
  Running command git checkout -q 0916b5b29b092afcbf2b898caae49abe80662bac
  Resolved https://github.com/pytorch/ao.git to commit 0916b5b29b092afcbf2b898caae49abe80662bac
  Preparing metadata (setup.py) ... done
  Created wheel for torchao: filename=torchao-0.5.0+git0916b5b2-cp310-cp310-linux_x86_64.whl size=4156208 sha256=a8101728cbbc66ed275dc5dcf5139143ea88f79501343790de6095ba29d0a2b8
  Stored in directory: /root/.cache/pip/wheels/09/a1/0b/ea6cc082439c4a26e121c33f0a44d6

## **Step 2. Download Llama 3.2 1B/3B models**

In [ ]:
from huggingface_hub import login
login()

In [5]:
!huggingface-cli download meta-llama/Llama-3.2-1B-Instruct --local-dir /content/models/Llama-3.2-1B-Instruct --local-dir-use-symlinks False

/usr/local/lib/python3.10/dist-packages/huggingface_hub/commands/download.py:139: FutureWarning: Ignoring --local-dir-use-symlinks. Downloading to a local directory does not use symlinks anymore.
  warnings.warn(
Fetching 13 files:   0% 0/13 [00:00<?, ?it/s]Downloading 'LICENSE.txt' to '/content/models/Llama-3.2-1B-Instruct/.cache/huggingface/download/LICENSE.txt.085b47c1575cb889b7024030e60b78f54f0b8c9e.incomplete'

LICENSE.txt: 100% 7.71k/7.71k [00:00<00:00, 16.9MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/LICENSE.txt

config.json: 100% 877/877 [00:00<00:00, 5.01MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/config.json

USE_POLICY.md: 100% 6.02k/6.02k [00:00<00:00, 17.0MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/USE_POLICY.md

generation_config.json: 100% 189/189 [00:00<00:00, 1.05MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/generation_config.json

README

## **Step 3: Export to ExecuTorch**

In [23]:
!cd /content/executorch; python -m executorch.examples.models.llama.export_llama \
  --checkpoint /content/models/Llama-3.2-1B-Instruct/original/consolidated.00.pth \
  --params /content/models/Llama-3.2-1B-Instruct/original/params.json \
  -kv \
  --use_sdpa_with_kv_cache \
  -X \
  -d bf16 \
  --metadata '{"get_bos_id":128000, "get_eos_ids":[128009, 128001]}' \
  --output_name="Llama-3.2-1B-Instruct.pte"

RuntimeError: module was compiled against NumPy C-API version 0x10 (NumPy 1.23) but the running NumPy has C-API version 0xe. Check the section C-API incompatibility at the Troubleshooting ImportError section at https://numpy.org/devdocs/user/troubleshooting-importerror.html#c-api-incompatibility for indications on how to solve this problem.
The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.
0it [00:00, ?it/s]
2024-11-23 11:16:16.775519: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-11-23 11:16:16.800709: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already b

In [24]:
!mv /content/executorch/Llama-3.2-1B-Instruct.pte /content/models/Llama-3.2-1B-Instruct/original/

## **Step 4: Upload to HF**

In [25]:
!huggingface-cli upload executorch-community/Llama-3.2-1B-Instruct /content/models/Llama-3.2-1B-Instruct/original/ --exclude="*.pth"

Consider using `hf_transfer` for faster uploads. This solution comes with some limitations. See https://huggingface.co/docs/huggingface_hub/hf_transfer for more details.
Start hashing 3 files.
Finished hashing 3 files.
Llama-3.2-1B-Instruct.pte:   0% 0.00/2.47G [00:00<?, ?B/s]
Upload 2 LFS files:   0% 0/2 [00:00<?, ?it/s]

tokenizer.model:   0% 0.00/2.18M [00:00<?, ?B/s]

tokenizer.model: 100% 2.18M/2.18M [00:00<00:00, 7.79MB/s]
Llama-3.2-1B-Instruct.pte: 100% 2.47G/2.47G [00:52<00:00, 47.5MB/s]

Upload 2 LFS files: 100% 2/2 [00:52<00:00, 26.18s/it]
https://huggingface.co/executorch-community/Llama-3.2-1B-Instruct/tree/main/.
